In [3]:
import torch 
import numpy as np 
import os 

In [4]:
data_root = '../HateXplain/Data/'

os.listdir (data_root)

['classes_two.npy',
 'glove.42B.300d_w2v.txt',
 'glove.42B.300d.zip',
 'word2vec.model.vectors.npy',
 'dataset.json',
 'Total_data_normal_softmax_1_128_2',
 'glove.42B.300d.txt',
 'word2vec.model',
 'post_id_divisions.json',
 '.ipynb_checkpoints',
 'Total_data_normal_softmax_1_128_2.pickle',
 'classes.npy',
 'README.md']

In [5]:
import json 

with open(data_root + 'dataset.json') as f:
    data = json.load(f)

In [56]:
data

{'1179055004553900032_twitter': {'post_id': '1179055004553900032_twitter',
  'annotators': [{'label': 'normal', 'annotator_id': 1, 'target': ['None']},
   {'label': 'normal', 'annotator_id': 2, 'target': ['None']},
   {'label': 'normal', 'annotator_id': 3, 'target': ['None']}],
  'rationales': [],
  'post_tokens': ['i',
   'dont',
   'think',
   'im',
   'getting',
   'my',
   'baby',
   'them',
   'white',
   '9',
   'he',
   'has',
   'two',
   'white',
   'j',
   'and',
   'nikes',
   'not',
   'even',
   'touched']},
 '1179063826874032128_twitter': {'post_id': '1179063826874032128_twitter',
  'annotators': [{'label': 'normal', 'annotator_id': 1, 'target': ['None']},
   {'label': 'normal', 'annotator_id': 2, 'target': ['None']},
   {'label': 'normal', 'annotator_id': 3, 'target': ['None']}],
  'rationales': [],
  'post_tokens': ['we',
   'cannot',
   'continue',
   'calling',
   'ourselves',
   'feminists',
   'if',
   'the',
   'rights',
   'of',
   'all',
   'womxn',
   'arent',
 

In [5]:
for k in data.keys():
    # print (len(data[k]['post_tokens']))
    post_tokens = data[k]['post_tokens']
    for tk in post_tokens:
        if '-' in tk:
            print (tk)

-o-
-.-
-.-
-o-
-_-
-_-
-_-


In [6]:
data_np = np.load(data_root + 'classes.npy')

In [58]:
data_np

array(['hatespeech', 'normal', 'offensive'], dtype='<U10')

In [7]:
from datasets import  load_dataset

# ds = load_dataset('json' , data_files= data_root + 'dataset.json')

ds = load_dataset('hatexplain')


In [9]:
ds

DatasetDict({
    train: Dataset({
        features: ['id', 'annotators', 'rationales', 'post_tokens'],
        num_rows: 15383
    })
    validation: Dataset({
        features: ['id', 'annotators', 'rationales', 'post_tokens'],
        num_rows: 1922
    })
    test: Dataset({
        features: ['id', 'annotators', 'rationales', 'post_tokens'],
        num_rows: 1924
    })
})

In [8]:
from datasets import load_dataset, DatasetDict

# Define a function to preprocess the dataset
def preprocess(example):
    # Rename the 'post_tokens' feature to 'text'
    example['text'] = ' '.join(example['post_tokens'])
    example['label'] = max(example['annotators']['label'], key=example['annotators']['label'].count)
    del example['post_tokens']
    del example['rationales']
    return example

# Apply the preprocessing function to each split of the dataset
dataset = DatasetDict({
    split: ds[split].map(preprocess)
    for split in ds.keys()
})



In [11]:
dataset

DatasetDict({
    train: Dataset({
        features: ['id', 'annotators', 'text', 'label'],
        num_rows: 15383
    })
    validation: Dataset({
        features: ['id', 'annotators', 'text', 'label'],
        num_rows: 1922
    })
    test: Dataset({
        features: ['id', 'annotators', 'text', 'label'],
        num_rows: 1924
    })
})

In [12]:
dataset['train'][0]

{'id': '23107796_gab',
 'annotators': {'label': [0, 2, 2],
  'annotator_id': [203, 204, 233],
  'target': [['Hindu', 'Islam'],
   ['Hindu', 'Islam'],
   ['Hindu', 'Islam', 'Other']]},
 'text': 'u really think i would not have been raped by feral hindu or muslim back in india or bangladesh and a neo nazi would rape me as well just to see me cry',
 'label': 2}

In [9]:
from transformers import AutoTokenizer

tokenizer = AutoTokenizer.from_pretrained("bert-base-uncased")
# tokenizer = AutoTokenizer.from_pretrained("xlnet-base-cased")


In [10]:
def preprocess_function(examples):
    return tokenizer(examples["text"], truncation=True)

In [11]:
tokenized_dataset = dataset.map(preprocess_function, batched=True)

Map:   0%|          | 0/1924 [00:00<?, ? examples/s]

In [12]:
from transformers import DataCollatorWithPadding

data_collator = DataCollatorWithPadding(tokenizer=tokenizer)

2024-04-16 07:52:01.785178: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2024-04-16 07:52:01.851284: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-04-16 07:52:02.866208: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


In [13]:
id2label = {0: "hate", 1: "normal", 2: "offense"}
label2id = {"hate": 0, "normal": 1, "offense": 2}

In [16]:
from transformers import AutoModelForSequenceClassification, TrainingArguments, Trainer

model = AutoModelForSequenceClassification.from_pretrained(
    "bert-base-uncased", num_labels=3, id2label=id2label, label2id=label2id
)

# model = AutoModelForSequenceClassification.from_pretrained(
#     "xlnet-base-cased", num_labels=3, id2label=id2label, label2id=label2id
# )

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [19]:
import evaluate

accuracy = evaluate.load("accuracy")

import numpy as np

'''
def compute_metrics(eval_pred):
    predictions, labels = eval_pred
    predictions = np.argmax(predictions, axis=1)
    return accuracy.compute(predictions=predictions, references=labels)
'''

'\ndef compute_metrics(eval_pred):\n    predictions, labels = eval_pred\n    predictions = np.argmax(predictions, axis=1)\n    return accuracy.compute(predictions=predictions, references=labels)\n'

In [20]:
import evaluate

f1_metric = evaluate.load("f1")

import numpy as np


def compute_metrics(eval_pred):
    predictions, labels = eval_pred
    predictions = np.argmax(predictions, axis=1)
    dict_f1 = f1_metric.compute(predictions=predictions, references=labels, average = 'macro')
    return dict_f1 
                            # accuracy.compute(predictions=predictions, references=labels)

In [21]:
! rm -r bert_base
! rm -r ./hf_logs/bert_base/

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


In [22]:
training_args = TrainingArguments(
    output_dir="bert_base",
    learning_rate=1e-5,
    per_device_train_batch_size=16,
    per_device_eval_batch_size=16,
    num_train_epochs=5,
    weight_decay=0.1,
    evaluation_strategy="epoch",
    save_strategy="epoch",
    load_best_model_at_end=True,
    push_to_hub=False,
    logging_strategy = "epoch",
    logging_steps=500,
    report_to="tensorboard",
    logging_dir="./hf_logs/bert_base/"
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=tokenized_dataset["train"],
    eval_dataset=tokenized_dataset["validation"],
    tokenizer=tokenizer,
    data_collator=data_collator,
    compute_metrics=compute_metrics,
    
)

trainer.train()

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
/raid/biplab/saikat/miniconda3/envs/nlp_mid/lib/python3.8/site-packages/accelerate/accelerator.py:436: FutureWarning: Passing the following arguments to `Accelerator` is deprecated and will be removed in version 1.0 of Accelerate: dict_keys(['dispatch_batches', 'split_batches', 'even_batches', 'use_seedable_sampler']). Please pass an `accelerate.DataLoaderConfiguration` instead: 
dataloader_config = DataLoaderConfiguration(dispatch_batches=None, split_batches=False, even_batches=True, use_seedable_sampler=True)
  warnings.warn(


TrainOutput(global_step=4810, training_loss=0.5946337725665118, metrics={'train_runtime': 309.3407, 'train_samples_per_second': 248.642, 'train_steps_per_second': 15.549, 'total_flos': 2365487265119580.0, 'train_loss': 0.5946337725665118, 'epoch': 5.0})

In [25]:
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=tokenized_dataset["train"],
    eval_dataset=tokenized_dataset["test"],
    tokenizer=tokenizer,
    compute_metrics=compute_metrics,
)

evaluation_metrics = trainer.evaluate()


/raid/biplab/saikat/miniconda3/envs/nlp_mid/lib/python3.8/site-packages/accelerate/accelerator.py:436: FutureWarning: Passing the following arguments to `Accelerator` is deprecated and will be removed in version 1.0 of Accelerate: dict_keys(['dispatch_batches', 'split_batches', 'even_batches', 'use_seedable_sampler']). Please pass an `accelerate.DataLoaderConfiguration` instead: 
dataloader_config = DataLoaderConfiguration(dispatch_batches=None, split_batches=False, even_batches=True, use_seedable_sampler=True)
  warnings.warn(


In [26]:
evaluation_metrics

{'eval_loss': 0.7146347761154175,
 'eval_f1': 0.6750896575285168,
 'eval_runtime': 2.1805,
 'eval_samples_per_second': 882.379,
 'eval_steps_per_second': 55.493}

# Visualisation

In [14]:
from bertviz import head_view, model_view
from transformers import BertTokenizer, BertModel



In [17]:
model = AutoModelForSequenceClassification.from_pretrained("./bert_base/checkpoint-4810", output_attentions=True)

In [18]:
test_data_len = len(dataset['test'])

In [25]:

test_idx = np.random.randint(test_data_len)

sentence_a = dataset['test'][test_idx]['text']
gt_label = dataset['test'][test_idx]['label'] 

inputs = tokenizer(sentence_a, return_tensors='pt')

input_ids = inputs['input_ids']
token_type_ids = inputs['token_type_ids']

# attention = model(input_ids, token_type_ids=token_type_ids)[-1]
outs = model(input_ids, token_type_ids=token_type_ids) #[-1]

attention = outs[-1]

In [26]:
predicted_cls = data_np[torch.argmax(outs[0]).item()]
gt_cls = data_np[gt_label]

print(f"Predicted: {predicted_cls}")
print(f"GT: {gt_cls}")


Predicted: offensive
GT: offensive


In [27]:
input_id_list = input_ids[0].tolist() # Batch index 0

tokens = tokenizer.convert_ids_to_tokens(input_id_list) 

In [28]:
head_view(attention, tokens)

<IPython.core.display.Javascript object>

In [37]:
len(attention)

12